In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function
import numpy as np
import tensorflow as tf

In [4]:
def cnn_model_fn(features, labels, mode):
  
    input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])
  
    #first conv and pool layer
    conv1 = tf.layers.conv2d(
          inputs=input_layer,
          filters=32,
          kernel_size=[5, 5],
          padding="same",
          activation=tf.nn.relu)
    pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)
    
    #second conv and pool layer
    conv2 = tf.layers.conv2d(
          inputs=pool1,
          filters=64,
          kernel_size=[5, 5],
          padding="same",
          activation=tf.nn.relu)
    pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)
    
    #hidden layer. Dropout regularization for overfitting
    pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])
    dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)
    dropout = tf.layers.dropout(inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)
    
    #output layer. 10 neurons for 0-9
    logits = tf.layers.dense(inputs=dropout, units=10)
    
    predictions = {
    "classes": tf.argmax(input=logits, axis=1),
    "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
    }
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)
    
    #cross entropy as loss function
    onehot_labels = tf.one_hot(indices=tf.cast(labels, tf.int32), depth=10)
    loss = tf.losses.softmax_cross_entropy(
    onehot_labels=onehot_labels, logits=logits)
    
    #configure training model to minimize loss with SGD
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
        train_op = optimizer.minimize(loss=loss,global_step=tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)
    #accuracy for eval
    eval_metric_ops = {
          "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)

In [5]:
def main(unused_argv):
    mnist = tf.contrib.learn.datasets.load_dataset("mnist")
    train_data = mnist.train.images 
    train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
    eval_data = mnist.test.images 
    eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)
    
    mnist_classifier = tf.estimator.Estimator(model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")
    tensors_to_log = {"probabilities": "softmax_tensor"}
    logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=50)
    
    #train model
    train_input_fn = tf.estimator.inputs.numpy_input_fn(
                        x={"x": train_data},
                        y=train_labels,
                        batch_size=100,
                        num_epochs=None,
                        shuffle=True)
    mnist_classifier.train(
                        input_fn=train_input_fn,
                        steps=20000,
                        hooks=[logging_hook])
    #model eval
    eval_input_fn = tf.estimator.inputs.numpy_input_fn(
                        x={"x": eval_data},
                        y=eval_labels,
                        num_epochs=1,
                        shuffle=False)
    eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
    print(eval_results)

In [ ]:
if __name__ == "__main__":
  tf.app.run()

Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Extracting MNIST-data\train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Extracting MNIST-data\train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data\t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data\t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x00000189A04AFB38>, '_task_type': 'worker', '_task_id': 0, '_master': '', '_is_chief': True, '_num_ps

INFO:tensorflow:loss = 2.30893, step = 1
INFO:tensorflow:probabilities = [[ 0.10722291  0.09787706  0.09882781  0.09156729  0.09863373  0.09843734
   0.09424321  0.10218988  0.10070085  0.11029994]
 [ 0.11410817  0.10756475  0.10228808  0.09433266  0.09206004  0.08171797
   0.09872806  0.10426565  0.09172893  0.11320575]
 [ 0.1063372   0.1007729   0.11156565  0.09096048  0.10232205  0.09120243
   0.09795135  0.10136025  0.10029228  0.09723533]
 [ 0.10431107  0.10188887  0.09391531  0.0962767   0.08918107  0.10413769
   0.10268588  0.1028131   0.09400836  0.11078192]
 [ 0.12352907  0.08943743  0.11239013  0.0917978   0.08821423  0.09221661
   0.09678224  0.10425299  0.08997935  0.11140007]
 [ 0.09906542  0.09506045  0.10348763  0.0988344   0.0883553   0.10083005
   0.09094796  0.10734435  0.11293441  0.10313994]
 [ 0.11352191  0.0981472   0.09948313  0.08762614  0.0924981   0.10651327
   0.10359477  0.10056613  0.09331675  0.1047326 ]
 [ 0.12285607  0.09798975  0.11127552  0.08214197  0

INFO:tensorflow:global_step/sec: 3.22659
INFO:tensorflow:probabilities = [[ 0.10491589  0.10053796  0.09318174  0.08722126  0.09332465  0.08710355
   0.11459333  0.10057736  0.09427837  0.12426592]
 [ 0.11168334  0.10074326  0.10188213  0.08654724  0.09850626  0.09428798
   0.09325173  0.10726083  0.09059922  0.11523803]
 [ 0.1103478   0.09457976  0.09783269  0.09363295  0.09996111  0.09666352
   0.09701836  0.1030906   0.10112084  0.10575236]
 [ 0.1078202   0.09610704  0.10098489  0.08799975  0.09401786  0.10074696
   0.10286738  0.10509887  0.09848393  0.10587315]
 [ 0.1155633   0.09513403  0.10900512  0.09637797  0.09231538  0.08941572
   0.10198875  0.09637327  0.1018323   0.1019942 ]
 [ 0.10570124  0.09832985  0.10313082  0.09569452  0.09073845  0.10299045
   0.1028702   0.09960064  0.08999079  0.1109531 ]
 [ 0.10486612  0.1057854   0.09772673  0.08906614  0.09639321  0.10292548
   0.10066544  0.09943857  0.09351213  0.1096208 ]
 [ 0.10158994  0.09137672  0.1090392   0.10426361  0

INFO:tensorflow:loss = 2.30668, step = 101 (31.005 sec)
INFO:tensorflow:probabilities = [[ 0.11173268  0.09971659  0.10630954  0.09339071  0.09847475  0.08896727
   0.10004283  0.09573449  0.08904961  0.11658158]
 [ 0.11105133  0.09878559  0.09917913  0.09863102  0.0885138   0.09464116
   0.09167476  0.11703202  0.09958311  0.1009081 ]
 [ 0.11578877  0.08729848  0.11290815  0.09381309  0.08719324  0.08717552
   0.1006479   0.10022811  0.09651271  0.11843405]
 [ 0.11011858  0.07829127  0.10269255  0.09342345  0.0986217   0.08796776
   0.10238929  0.10334785  0.11168091  0.11146663]
 [ 0.11236338  0.09963519  0.0994377   0.09565848  0.09368579  0.09698162
   0.09991457  0.10191564  0.09572936  0.1046783 ]
 [ 0.09055052  0.10439559  0.11111996  0.09039314  0.09662975  0.08687577
   0.11209816  0.09356289  0.10251153  0.1118627 ]
 [ 0.13133527  0.10214349  0.11354096  0.08393562  0.08374439  0.09921043
   0.09407423  0.10543681  0.09268307  0.09389575]
 [ 0.10785151  0.10500523  0.09509061

INFO:tensorflow:global_step/sec: 3.29025
INFO:tensorflow:probabilities = [[ 0.1089571   0.08014086  0.10743329  0.0941348   0.09423395  0.09909882
   0.10149746  0.10557272  0.09724192  0.11168908]
 [ 0.11362234  0.08667212  0.10970245  0.09233095  0.08352333  0.09351061
   0.08989634  0.1095167   0.11270214  0.10852304]
 [ 0.10489983  0.09370727  0.09726842  0.08528575  0.09294839  0.10084756
   0.10137419  0.10086635  0.10514197  0.11766028]
 [ 0.10005846  0.08626702  0.09651256  0.10336845  0.0948713   0.09495878
   0.10707294  0.1038071   0.1050824   0.10800106]
 [ 0.11037183  0.08753578  0.11511046  0.09266751  0.09909364  0.09518944
   0.10581016  0.09565105  0.08994211  0.10862802]
 [ 0.10937377  0.09240492  0.09157315  0.08820053  0.09652296  0.09280641
   0.09620272  0.10338054  0.10907169  0.12046325]
 [ 0.11687675  0.0894588   0.09228317  0.09283803  0.10114173  0.09435991
   0.10499945  0.10385992  0.09729595  0.10688638]
 [ 0.11454076  0.08705343  0.10923751  0.08720957  0

...

INFO:tensorflow:loss = 0.19425, step = 19701 (30.225 sec)
INFO:tensorflow:probabilities = [[ 0.0000065   0.00000017  0.00022404  0.00001433  0.00119822  0.00002079
   0.99785906  0.00003924  0.00063719  0.00000033]
 [ 0.00000903  0.00002117  0.00003986  0.00000051  0.00015013  0.00011974
   0.99961025  0.00000002  0.00004916  0.00000013]
 [ 0.00001561  0.00000541  0.99958712  0.00008182  0.00001484  0.00001797
   0.00022938  0.00000524  0.00004044  0.00000226]
 [ 0.0241748   0.00259085  0.00364076  0.00628928  0.06172088  0.02516333
   0.83445936  0.00469422  0.01680653  0.02045998]
 [ 0.00001149  0.00000022  0.0000007   0.00002154  0.00348037  0.00003682
   0.00000054  0.0060966   0.00007364  0.99027807]
 [ 0.00025183  0.00000123  0.9977271   0.00197272  0.00000031  0.0000008
   0.00000022  0.00000603  0.00001702  0.00002261]
 [ 0.00200016  0.0104358   0.01937112  0.40046898  0.00015075  0.55306292
   0.00006421  0.00384145  0.00240046  0.00820419]
 [ 0.0000023   0.          0.0000001

INFO:tensorflow:global_step/sec: 2.64028
INFO:tensorflow:probabilities = [[ 0.99990618  0.00000001  0.00002239  0.00000058  0.          0.00000096
   0.00000003  0.00000042  0.00000013  0.0000694 ]
 [ 0.00012944  0.0000359   0.00000916  0.00351807  0.00049129  0.9888131
   0.00033651  0.00007651  0.00125262  0.00533724]
 [ 0.00013163  0.00000544  0.00000062  0.00257108  0.0000133   0.99656445
   0.00065378  0.00001519  0.00004196  0.00000259]
 [ 0.00000353  0.          0.00000135  0.00010178  0.          0.99966657
   0.00000029  0.          0.00022522  0.00000127]
 [ 0.0001112   0.0174062   0.00087275  0.04840376  0.00317975  0.00131896
   0.00000802  0.01981641  0.00908422  0.89979875]
 [ 0.00002635  0.00000008  0.00043763  0.00000123  0.99279565  0.00010394
   0.00466919  0.00000523  0.00003927  0.00192158]
 [ 0.00018726  0.00002562  0.00007751  0.00027132  0.00004766  0.00121791
   0.00028446  0.00000219  0.99784601  0.00004013]
 [ 0.00000011  0.00000002  0.00001082  0.00000004  0.

INFO:tensorflow:loss = 0.115268, step = 19801 (37.906 sec)
INFO:tensorflow:probabilities = [[ 0.00000716  0.00000043  0.00000098  0.00000723  0.00000209  0.00000336
   0.          0.99447566  0.00000133  0.00550178]
 [ 0.00004706  0.00001132  0.00001275  0.0000393   0.00157959  0.00004067
   0.00000003  0.99139774  0.00005539  0.00681614]
 [ 0.00000035  0.00000001  0.00000677  0.99951053  0.          0.00047047
   0.00000005  0.          0.00001124  0.00000065]
 [ 0.00021907  0.00000061  0.00002981  0.00002303  0.00000627  0.00002339
   0.00000001  0.99442625  0.00004391  0.0052277 ]
 [ 0.00001591  0.99057674  0.0005288   0.00133594  0.00150372  0.00002934
   0.00006769  0.00534714  0.00041868  0.00017608]
 [ 0.01048585  0.02432638  0.01080796  0.00224971  0.00049006  0.13299063
   0.79586351  0.00011155  0.02259007  0.00008433]
 [ 0.00000084  0.00000102  0.00001354  0.00005955  0.0110849   0.00044406
   0.00000068  0.03863179  0.00058838  0.9491753 ]
 [ 0.00000369  0.00000007  0.00000

INFO:tensorflow:global_step/sec: 2.46308
INFO:tensorflow:probabilities = [[ 0.0001559   0.00001352  0.00070421  0.01987997  0.00072226  0.00533406
   0.00011941  0.00017564  0.53882688  0.43406817]
 [ 0.00032044  0.0317943   0.00208105  0.00001406  0.00090198  0.00872307
   0.94838667  0.0000012   0.0077744   0.00000267]
 [ 0.00000931  0.00000064  0.00001463  0.99750572  0.00000015  0.00238869
   0.00000045  0.00000416  0.00001684  0.00005932]
 [ 0.03694372  0.00066429  0.00403127  0.00079727  0.00578955  0.76471275
   0.17908959  0.0004216   0.0057682   0.00178174]
 [ 0.00028668  0.00323364  0.00531931  0.00069608  0.84090149  0.00421606
   0.08900155  0.00033813  0.05567298  0.00033396]
 [ 0.00000175  0.0003114   0.91723365  0.005814    0.00058272  0.00019595
   0.0019567   0.07262018  0.00127135  0.00001241]
 [ 0.00000732  0.00000126  0.00001563  0.00033806  0.00116404  0.00001006
   0.00000013  0.0212832   0.00007733  0.97710299]
 [ 0.0000016   0.0000117   0.00001536  0.00005343  0

INFO:tensorflow:loss = 0.0995213, step = 19901 (40.564 sec)
INFO:tensorflow:probabilities = [[ 0.00000004  0.00015419  0.99942303  0.00040676  0.          0.00000013
   0.00000077  0.00000145  0.00001371  0.        ]
 [ 0.00000035  0.          0.00000024  0.00000297  0.00009084  0.00000031
   0.          0.9964819   0.00000473  0.00341866]
 [ 0.00007468  0.00000009  0.00000136  0.00096613  0.00028077  0.95193917
   0.00000043  0.00046565  0.00254951  0.04372216]
 [ 0.99130648  0.00000041  0.00002429  0.00089885  0.00000006  0.00740691
   0.00002094  0.00031254  0.00001671  0.00001276]
 [ 0.00000004  0.0001063   0.9994399   0.00013601  0.00000004  0.00000001
   0.00000021  0.00031612  0.00000122  0.00000006]
 [ 0.00000584  0.99867046  0.00002544  0.00056028  0.00004014  0.000008
   0.00000922  0.00000835  0.00066558  0.00000683]
 [ 0.00019486  0.00000941  0.25407156  0.71615261  0.00000162  0.00042986
   0.00000115  0.00003499  0.02683303  0.00227092]
 [ 0.00000423  0.99657637  0.000404